# EFM Imaging

This is an example using `scopyon` (https://scopyon.readthedocs.io/).

In [1]:
import scopyon

Set the configuration first.

In [2]:
config = scopyon.DefaultConfiguration()
config.default.magnification = 360.0
config.default.detector.exposure_time = 33.0e-3  # second
config.default.detector.image_size = [128, 128]

In [3]:
# config.environ.processes = 20

A field of microscopic view could be calculated as follows:

In [4]:
pixel_length = config.default.detector.pixel_length / config.default.magnification
L_2 = config.default.detector.image_size[0] * pixel_length * 0.5

Randomly generate positions of 30 molecules on membrane.

In [5]:
import numpy
rng = numpy.random.RandomState(1)
num_frames = 100
dt = config.default.detector.exposure_time
t = numpy.linspace(0, dt, num_frames + 1)
depth = 0.5e-6  # m

In [6]:
Nm = 30
Dm = 0.1e-12  # m ** 2 / s
inputs1 = scopyon.sample_inputs(t, N=Nm, lower=(-L_2, -L_2, 0.0), upper=(+L_2, +L_2, 0.0), ndim=2, D=Dm, rng=rng)

In [7]:
scopyon.form_image(inputs1, config=config, rng=rng)

Next, 244 molecules (corresponding to 100 nM) are distributed in volume.

In [8]:
Nc = 244  # ~100 nM
Dc = 5.0e-12  # m ** 2 / s
inputs2 = scopyon.sample_inputs(t, N=Nc, lower=(-L_2, -L_2, -depth), upper=(+L_2, +L_2, 0.0), ndim=3, D=Dc, start=Nm, rng=rng)

In [9]:
inputs = [(inputs1_[0], numpy.vstack((inputs1_[1], inputs2_[1]))) for inputs1_, inputs2_ in zip(inputs1, inputs2)]

`scopyon.form_image` generates a single image from the given inputs.

In [10]:
# import logging
# logging.basicConfig(level=logging.INFO)

In [11]:
img = scopyon.form_image(inputs, config=config, rng=rng)

In [12]:
img

TIRF Imaging is the special case, where source angle exceeds critical angle. When source angle is less than critical angle, penetration depth is assumed to be infinity (Oblique illumination).

In [13]:
# theta = numpy.arcsin(1.384 / 1.46) = 1.2467198316493195  # Critical Angle
config.default.light_source.angle = 1.24
config.default.light_source.flux_density = config.default.light_source.flux_density * 3.977927479215699

Only the molecules on the focal plane:

In [14]:
scopyon.form_image(inputs1, config=config, rng=rng)

With the molecules in volume:

In [15]:
scopyon.form_image(inputs, config=config, rng=rng)